In [1]:
import sys
sys.path.insert(0, '../../')
import ccal
%matplotlib inline
%config InlineBackend.figure_formats = {'svg',}

import numpy as np
import pandas as pd

from sklearn.cluster import AgglomerativeClustering
from scipy.cluster.hierarchy import linkage, fcluster, cophenet
from scipy.spatial.distance import pdist
from sklearn import manifold
from statsmodels.nonparametric.kernel_density import KDEMultivariate
import matplotlib as mpl
import matplotlib.pyplot as plt
import matplotlib.tri as tri
import matplotlib.cm as cm

import numpy as np
import rpy2.robjects as ro
from rpy2.robjects.numpy2ri import numpy2ri
ro.conversion.py2ri = numpy2ri
from rpy2.robjects.packages import importr
mass = importr('MASS')

==================== Computational Cancer Analysis Library ====================
<14:44:46> Checking dependencies ...
<14:44:46> Using the following packages:
<14:44:46> 	matplotlib (v1.5.1)
<14:44:46> 	numpy (v1.10.4)
<14:44:46> 	pandas (v0.18.0)
<14:44:46> 	rpy2 (v2.7.9)
<14:44:46> 	scikit-learn (v0.17.1)
<14:44:46> 	scipy (v0.17.0)
<14:44:46> 	seaborn (v0.7.0)


# get_states

In [2]:
h_matrix = ccal.support.read_gct('../../../hematopoietic_cancer/result/ccle_hema/k9/ccle_hema_k_9_H.gct')

ks = [1, 2, 3]

nclustering = 3

CMAP_CATEGORICAL = ccal.visualize.CMAP_CATEGORICAL
print_log = ccal.support.print_log

In [3]:
# H's row - row mean and / row std
standardized_h_matrix = ccal.support.standardize_pandas_object(h_matrix)
standardized_h_matrix

A3KAW_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE  \
nmf_compC1_9                                 -0.539879   
nmf_compC2_9                                  0.412136   
nmf_compC3_9                                 -0.499819   
nmf_compC4_9                                  0.452953   
nmf_compC5_9                                 -0.253993   
nmf_compC6_9                                 -0.685155   
nmf_compC7_9                                 -0.446383   
nmf_compC8_9                                  2.022634   
nmf_compC9_9                                 -0.460068   

              A4FUK_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE  \
nmf_compC1_9                                 -0.653274   
nmf_compC2_9                                  0.251295   
nmf_compC3_9                                 -0.502230   
nmf_compC4_9                                 -0.075154   
nmf_compC5_9                                 -0.385266   
nmf_compC6_9                                 -0.203721   
nmf_compC7_9                                 -0.268137   
nmf_compC8_9                                  2.270094   
nmf_compC9_9                                 -0.539585   

              ALLSIL_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE  \
nmf_compC1_9                                  -0.694367   
nmf_compC2_9                                  -0.203681   
nmf_compC3_9                                  -0.499065   
nmf_compC4_9                                  -0.347020   
nmf_compC5_9                                   2.932948   
nmf_compC6_9                                  -0.345414   
nmf_compC7_9                                  -0.331704   
nmf_compC8_9                                  -0.640372   
nmf_compC9_9                                   0.192454   

              AML193_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE  \
nmf_compC1_9                                  -0.758196   
nmf_compC2_9                                   0.080619   
nmf_compC3_9                                  -0.237520   
nmf_compC4_9                                  -0.572833   
nmf_compC5_9                                  -0.072358   
nmf_compC6_9                                  -0.315288   
nmf_compC7_9                                   2.235296   
nmf_compC8_9                                  -0.445370   
nmf_compC9_9                                  -0.470531   

              AMO1_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE  \
nmf_compC1_9                                -0.271413   
nmf_compC2_9                                -0.380598   
nmf_compC3_9                                -0.443297   
nmf_compC4_9                                 0.123151   
nmf_compC5_9                                -0.173752   
nmf_compC6_9                                -0.169885   
nmf_compC7_9                                -0.430184   
nmf_compC8_9                                 2.091734   
nmf_compC9_9                                -0.547612   

              BCP1_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE  \
nmf_compC1_9                                -0.492330   
nmf_compC2_9                                 0.203402   
nmf_compC3_9                                -0.456549   
nmf_compC4_9                                 0.830065   
nmf_compC5_9                                -0.091235   
nmf_compC6_9                                -0.685154   
nmf_compC7_9                                -0.456087   
nmf_compC8_9                                 1.574370   
nmf_compC9_9                                -0.306299   

              BDCM_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE  \
nmf_compC1_9                                 0.077991   
nmf_compC2_9                                -0.179652   
nmf_compC3_9                                -0.458142   
nmf_compC4_9                                -0.590894   
nmf_compC5_9                                -0.481660   
nmf_compC6_9                                 3.621661   
nmf_compC7_9                                -0.460124   
nmf_compC8_9                                -0.159632   
nmf_compC9_9   

In [4]:
# Clip values less than -3 and more than 3
standardized_clipped_h_matrix = standardized_h_matrix.clip(-3, 3)
standardized_clipped_h_matrix

A3KAW_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE  \
nmf_compC1_9                                 -0.539879   
nmf_compC2_9                                  0.412136   
nmf_compC3_9                                 -0.499819   
nmf_compC4_9                                  0.452953   
nmf_compC5_9                                 -0.253993   
nmf_compC6_9                                 -0.685155   
nmf_compC7_9                                 -0.446383   
nmf_compC8_9                                  2.022634   
nmf_compC9_9                                 -0.460068   

              A4FUK_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE  \
nmf_compC1_9                                 -0.653274   
nmf_compC2_9                                  0.251295   
nmf_compC3_9                                 -0.502230   
nmf_compC4_9                                 -0.075154   
nmf_compC5_9                                 -0.385266   
nmf_compC6_9                                 -0.203721   
nmf_compC7_9                                 -0.268137   
nmf_compC8_9                                  2.270094   
nmf_compC9_9                                 -0.539585   

              ALLSIL_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE  \
nmf_compC1_9                                  -0.694367   
nmf_compC2_9                                  -0.203681   
nmf_compC3_9                                  -0.499065   
nmf_compC4_9                                  -0.347020   
nmf_compC5_9                                   2.932948   
nmf_compC6_9                                  -0.345414   
nmf_compC7_9                                  -0.331704   
nmf_compC8_9                                  -0.640372   
nmf_compC9_9                                   0.192454   

              AML193_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE  \
nmf_compC1_9                                  -0.758196   
nmf_compC2_9                                   0.080619   
nmf_compC3_9                                  -0.237520   
nmf_compC4_9                                  -0.572833   
nmf_compC5_9                                  -0.072358   
nmf_compC6_9                                  -0.315288   
nmf_compC7_9                                   2.235296   
nmf_compC8_9                                  -0.445370   
nmf_compC9_9                                  -0.470531   

              AMO1_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE  \
nmf_compC1_9                                -0.271413   
nmf_compC2_9                                -0.380598   
nmf_compC3_9                                -0.443297   
nmf_compC4_9                                 0.123151   
nmf_compC5_9                                -0.173752   
nmf_compC6_9                                -0.169885   
nmf_compC7_9                                -0.430184   
nmf_compC8_9                                 2.091734   
nmf_compC9_9                                -0.547612   

              BCP1_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE  \
nmf_compC1_9                                -0.492330   
nmf_compC2_9                                 0.203402   
nmf_compC3_9                                -0.456549   
nmf_compC4_9                                 0.830065   
nmf_compC5_9                                -0.091235   
nmf_compC6_9                                -0.685154   
nmf_compC7_9                                -0.456087   
nmf_compC8_9                                 1.574370   
nmf_compC9_9                                -0.306299   

              BDCM_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE  \
nmf_compC1_9                                 0.077991   
nmf_compC2_9                                -0.179652   
nmf_compC3_9                                -0.458142   
nmf_compC4_9                                -0.590894   
nmf_compC5_9                                -0.481660   
nmf_compC6_9                                 3.000000   
nmf_compC7_9                                -0.460124   
nmf_compC8_9                                -0.159632   
nmf_compC9_9   

In [5]:
# Get association between samples
compared_matrix = ccal.analyze.compare_matrices(standardized_clipped_h_matrix, standardized_clipped_h_matrix, axis=1)
compared_matrix

<14:44:57> Comparing A3KAW_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE (1/166) vs. ...
<14:44:57> Comparing A4FUK_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE (2/166) vs. ...
<14:44:58> Comparing ALLSIL_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE (3/166) vs. ...
<14:44:58> Comparing AML193_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE (4/166) vs. ...
<14:44:59> Comparing AMO1_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE (5/166) vs. ...
<14:44:59> Comparing BCP1_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE (6/166) vs. ...
<14:45:00> Comparing BDCM_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE (7/166) vs. ...
<14:45:00> Comparing BL41_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE (8/166) vs. ...
<14:45:01> Comparing BL70_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE (9/166) vs. ...
<14:45:01> Comparing BV173_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE (10/166) vs. ...
<14:45:02> Comparing CA46_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE (11/166) vs. ...
<14:45:02> Comparing CI1_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE (12/166) vs. ...
<14:45:03> Comparing CMK_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE (13/166

A3KAW_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE  \
A3KAW_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                      0.890544   
A4FUK_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                      0.786964   
ALLSIL_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                    -0.163344   
AML193_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                    -0.175238   
AMO1_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                       0.668492   
BCP1_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                       0.869617   
BDCM_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                      -0.211889   
BL41_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                      -0.178949   
BL70_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                      -0.202694   
BV173_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                     -0.178307   
CA46_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                      -0.228060   
CI1_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                       -0.290458   
CMK_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                       -0.202013   
CMLT1_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                     -0.145201   
DAUDI_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                     -0.211417   
DB_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                        -0.221818   
DEL_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                        0.333027   
DND41_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                     -0.174876   
DOHH2_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                     -0.218252   
EB1_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                       -0.285310   
EHEB_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                      -0.192915   
EJM_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                        0.644607   
EM2_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                       -0.169047   
EOL1_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                      -0.207792   
F36P_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                      -0.188046   
GA10_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                      -0.183117   
GDM1_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                      -0.557865   
GRANTA519_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                 -0.260809   
HDLM2_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                      0.176638   
HDMYZ_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                      0.322465   
...                                                                                ...   
RI1_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                       -0.192618   
RL_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                        -0.226027   
RPMI8226_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                   0.679018   
RPMI8402_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                  -0.152809   
RS411_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                     -0.214059   
SEM_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                       -0.217012   
SET2_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                      -0.195046   
SIGM5_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                     -0.195115   
SKM1_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                      -0.171375   
SKMM2_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                      0.758064   
SR786_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                      0.288803   
ST486_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                     -0.194059   
SUDHL10_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE                                   -0.252657

In [6]:
# Samples' hierarchical cluster assignment per k (k x sample)
results = pd.DataFrame(index=ks, columns=list(h_matrix.columns) + ['cophenetic_correlation'])

for k in ks:
    print_log('Hierarchical clustering for k = {} ...'.format(k))
    
    # Hierarchical cluster the association between the samples and get labels cut-off at k (nclustering x sample)
    labels = pd.DataFrame(index=range(nclustering), columns=compared_matrix.index)
    for i in range(nclustering):
        ward = AgglomerativeClustering(n_clusters=k)
        ward.fit(compared_matrix)
        labels.iloc[i, :] = ward.labels_

    # Get the number of times samples co-cluster (sample x sample)
    cooccurences = pd.DataFrame(index=compared_matrix.index, columns=compared_matrix.index)
    cooccurences.fillna(0, inplace=True)
    for n, s in labels.iterrows():
        for i in s.index:
            for j in s.index:
                if i is j or s.ix[i] == s.ix[j]:
                    cooccurences.ix[i, j] += 1
    
    # Normalize
    cooccurences /= nclustering

    # Convert association to distance
    distances = 1 - cooccurences
    
    # Get the final cluster label cut-off at k
    ward = linkage(distances, method='ward')
    labels = fcluster(ward, k, criterion='maxclust')
    labels -= 1  # Convert from 1-based to 0-based indexing
    results.ix[k, h_matrix.columns] = labels
    
    # Compute the cophenetic correlation (the correlation between cophenetic and Euclidian distances)
    cophenetic_correlation = cophenet(ward, pdist(distances))[0]
    results.ix[k, 'cophenetic_correlation'] = cophenetic_correlation

results

<14:46:26> Hierarchical clustering for k = 1 ...
<14:46:46> Hierarchical clustering for k = 2 ...
<14:47:00> Hierarchical clustering for k = 3 ...


A3KAW_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE  \
1                                        0   
2                                        1   
3                                        1   

  A4FUK_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE  \
1                                        0   
2                                        1   
3                                        1   

  ALLSIL_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE  \
1                                         0   
2                                         1   
3                                         0   

  AML193_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE  \
1                                         0   
2                                         1   
3                                         0   

  AMO1_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE  \
1                                       0   
2                                       1   
3                                       1   

  BCP1_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE  \
1                                       0   
2                                       1   
3                                       1   

  BDCM_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE  \
1                                       0   
2                                       0   
3                                       2   

  BL41_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE  \
1                                       0   
2                                       0   
3                                       2   

  BL70_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE  \
1                                       0   
2                                       0   
3                                       2   

  BV173_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE          ...            \
1                                        0          ...             
2                                        1          ...             
3                                        0          ...             

  SUPT1_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE  \
1                                        0   
2                                        1   
3                                        0   

  TALL1_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE  \
1                                        0   
2                                        1   
3                                        0   

  TF1_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE  \
1                                      0   
2                                      1   
3                                      0   

  THP1_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE  \
1                                       0   
2                                       1   
3                                       0   

  TO175T_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE  \
1                                         0   
2                                         1   
3                                         0   

  TOLEDO_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE  \
1                                         0   
2                                         0   
3                                         2   

  U266B1_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE  \
1                                         0   
2                                         1   
3                                         1   

  U937_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE  \
1                                       0   
2                                       1   
3                                       0   

  WSUDLCL2_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE cophenetic_correlation  
1                                           0                    NaN  
2                                           0                      1  
3                                           2               0.990523  

[3 rows x 167 columns]

# map_onco_gps

In [18]:
states = 2

ngrid = 100

exp = 1.3

In [19]:
# Get components' x & y coordinates
mds = manifold.MDS()
components_coordinates = mds.fit_transform(standardized_clipped_h_matrix)
components_coordinates

array([[-11.98311659,  -6.12068377],
       [ -0.06929297,  -3.97622294],
       [  5.79051328,  11.84030341],
       [  3.80851448,   2.64552497],
       [-11.02763696,   4.33056597],
       [ -2.86752028, -11.30166025],
       [  9.363829  , -10.01224377],
       [ 12.96373553,   1.47921596],
       [ -5.97902549,  11.11520041]])

In [20]:
# Delaunay triangulate components' projection
delaunay = tri.Triangulation(components_coordinates[:, 0], components_coordinates[:, 1])

In [21]:
samples = pd.DataFrame(index=h_matrix.columns, columns=['state', 'x', 'y'])

# Get sample labels
samples.ix[:, 'state'] = results.ix[states, :]

# Get samples' x & y coordinates
for sample in h_matrix:
    col = h_matrix.ix[:, sample]
    third = col.sort_values()[-3]
    col = col.mask(col < third, other=0)
    # TODO: remove assertion
    assert sum(col != 0) == 3
    x = sum(col**exp * components_coordinates[:, 0]) / sum(col**exp)
    y = sum(col**exp * components_coordinates[:, 1]) / sum(col**exp)
    samples.ix[sample, ['x', 'y']] = x, y

samples

state          x         y
A3KAW_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE         1    9.49139   0.83463
A4FUK_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE         1    10.5305  0.898002
ALLSIL_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE        1   -9.79598   5.00705
AML193_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE        1    6.77414  -8.24583
AMO1_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE          1    9.92939   1.05736
BCP1_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE          1    8.94839   1.06771
BDCM_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE          0   -2.89653  -9.73983
BL41_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE          0   -9.03059   -4.1922
BL70_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE          0   -10.6456  -3.50379
BV173_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE         1   -6.02647   8.91914
CA46_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE          0   -11.1409   -2.6767
CI1_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE           0   -7.73153  -7.31538
CMK_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE           1    5.33423   10.5098
CMLT1_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE         1   -9.88149   4.59906
DAUDI_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE         0     -10.89  -5.80209
DB_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE            0   -9.83865  -3.65246
DEL_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE           1   0.597215  -3.37929
DND41_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE         1   -8.21273   5.26602
DOHH2_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE         0   -9.74652  -5.73528
EB1_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE           0    -7.9037  -7.76776
EHEB_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE          0   -3.52247  -10.3242
EJM_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE           1    10.3379  0.287524
EM2_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE           1    7.27024  -7.79874
EOL1_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE          1    7.57839  -9.80936
F36P_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE          1    5.03349   9.48505
GA10_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE          0   -11.4223  -3.65121
GDM1_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE          1    4.72607   3.73661
GRANTA519_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE     0   -3.25389  -8.23114
HDLM2_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE         1  -0.725234  -6.14439
HDMYZ_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE         1    2.43131   2.79094
...                                            ...        ...       ...
RI1_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE           0   -8.31505  -5.87598
RL_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE            0   -10.8391  -5.91969
RPMI8226_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE      1    10.0933  0.426219
RPMI8402_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE      1   -8.94826   4.85445
RS411_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE         1   -5.02337   6.09184
SEM_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE           1   -4.33407   4.81949
SET2_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE          1    5.47499   10.7678
SIGM5_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE         1    7.79246  -8.83405
SKM1_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE          1    8.77597  -7.83019
SKMM2_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE         1    11.2019   1.04287
SR786_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE         1 -0.0452529  -3.20936
ST486_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE         0   -7.91876 -0.581497
SUDHL10_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE       0   -9.88834  -3.93144
SUDHL1_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE        1 -0.0983978  -2.64847
SUDHL4_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE        0   -9.95773  -5.27712
SUDHL5_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE        0   -9.02274  -3.49784
SUDHL6_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE        0   -9.40512  -3.89159
SUDHL8_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE        0   -8.58165  0.388334
SUPB15_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE        1   -6.48618   8.18368
SUPM2_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE         1   0.135395  -3.71632
SUPT11_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE        1    -7.2303   3.01868
SUPT1_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE         1   -8.91187   4.70832
TALL1_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE         1   -8.80563   4.68552
TF1_HAEMATOPOIETIC_AND_LYMPHOID_TISSUE           1    5.24867   10.7062
THP1_HAEMATOP

In [25]:
# Get KDE at each grid intersection for each state
kdes = np.empty((states, ngrid, ngrid))
for s in range(states):
    coordiantes = samples.ix[samples.ix[:, 'state'] == s, ['x', 'y']]
    x = np.array(coordiantes.ix[:, 'x'], dtype=float)
    y = np.array(coordiantes.ix[:, 'y'], dtype=float)
    bandwidth_x = np.asarray(mass.bcv(x)[0])
    bandwidth_y = np.asarray(mass.bcv(y)[0])
    kde = mass.kde2d(x, y, np.asarray([bandwidth_x, bandwidth_y]), n=np.asarray([ngrid]))
    kdes[s] = np.array(kde[2])
    
kdes

array([[[  1.01956018e-04,   1.26564811e-04,   1.56348579e-04, ...,
           1.05905678e-03,   9.25486922e-04,   8.07001107e-04],
        [  1.10738059e-04,   1.37377906e-04,   1.69602283e-04, ...,
           1.17698282e-03,   1.03228718e-03,   9.03650869e-04],
        [  1.19561496e-04,   1.48211117e-04,   1.82844818e-04, ...,
           1.30784032e-03,   1.15156675e-03,   1.01229276e-03],
        ..., 
        [  9.77816618e-03,   1.01389587e-02,   1.04657250e-02, ...,
           5.98067808e-10,   4.58247947e-10,   3.59280746e-10],
        [  9.12727655e-03,   9.46607002e-03,   9.77295404e-03, ...,
           4.45857794e-10,   3.32049641e-10,   2.52479032e-10],
        [  8.46835954e-03,   8.78468995e-03,   9.07128205e-03, ...,
           3.40433850e-10,   2.47095914e-10,   1.82494663e-10]],

       [[  1.73110729e-06,   2.08113796e-06,   2.49270384e-06, ...,
           8.87033437e-04,   7.91375717e-04,   7.03241722e-04],
        [  2.25307063e-06,   2.69707536e-06,   3.21655420e-0

In [27]:
# Assign the best KDE probability and state for each grid intersection
grid_probabilities = np.empty((ngrid, ngrid))
grid_states = np.empty((ngrid, ngrid))
for i in range(ngrid):
    for j in range(ngrid):
        grid_probabilities[i, j] = max(kdes[:, i, j])
        grid_states[i, j] = np.argmax(kdes[:, i, j])
grid_states

array([[ 0.,  0.,  0., ...,  0.,  0.,  0.],
       [ 0.,  0.,  0., ...,  0.,  0.,  0.],
       [ 0.,  0.,  0., ...,  0.,  0.,  0.],
       ..., 
       [ 0.,  0.,  0., ...,  1.,  1.,  1.],
       [ 0.,  0.,  0., ...,  1.,  1.,  1.],
       [ 0.,  0.,  0., ...,  1.,  1.,  1.]])

## plot

In [29]:
fig, ax = plt.subplots(figsize=(8, 8))
colors = cm.ScalarMappable(norm=mpl.colors.Normalize(vmin=0, vmax=state), cmap=CMAP_CATEGORICAL)


# Plot triangles
ax.triplot(delaunay, color='blue', zorder=3)

# Plot samples
for idx, s in samples.iterrows():
    ax.plot(s.ix['x'], s.ix['y'],
            marker='o', markersize=15, markerfacecolor=colors.to_rgba(s.ix['state']), markeredgewidth=0.69, markeredgecolor='black',
           zorder=4)

xmin, xmax, ymin, ymax = ax.axis('off')
# Plot contour
ax.contour(np.linspace(xmin, xmax, num=ngrid), np.linspace(ymin, ymax, num=ngrid), grid_probabilities,
           levels=np.linspace(0, 1, 69), linewidths=1, colors='black',
           zorder=2)

# Plot background
for i in np.linspace(xmin, xmax, num=ngrid):
    for j in np.linspace(ymin, ymax, num=ngrid):
        ax.plot(i, j,
                marker='s', markersize=13.6, markerfacecolor=colors.to_rgba(grid_states[i, j]), alpha=5 * grid_probabilities[i, j],
               zorder=1)

/Applications/anaconda3/lib/python3.5/site-packages/ipykernel/__main__.py:24: DeprecationWarning: using a non-integer number instead of an integer will result in an error in the future
